In [1]:
!pip install bs4
!pip install requests

In [8]:
from bs4 import BeautifulSoup
import requests
url = requests.get('https://en.wikipedia.org/wiki/Main_Page')
soup = BeautifulSoup(url.text, 'html.parser')
story = soup.find_all(['h1', 'h2','h3'])
for i in story:
    print(i)

<h1 class="firstHeading mw-first-heading" id="firstHeading" style="display: none">Main Page</h1>
<h1><span class="mw-headline" id="Welcome_to_Wikipedia">Welcome to <a href="/wiki/Wikipedia" title="Wikipedia">Wikipedia</a></span></h1>
<h2 class="mp-h2" id="mp-tfa-h2"><span id="From_today.27s_featured_article"></span><span class="mw-headline" id="From_today's_featured_article">From today's featured article</span></h2>
<h2 class="mp-h2" id="mp-dyk-h2"><span class="mw-headline" id="Did_you_know_...">Did you know ...</span></h2>
<h2 class="mp-h2" id="mp-itn-h2"><span class="mw-headline" id="In_the_news">In the news</span></h2>
<h2 class="mp-h2" id="mp-otd-h2"><span class="mw-headline" id="On_this_day">On this day</span></h2>
<h2 class="mp-h2" id="mp-tfp-h2"><span id="Today.27s_featured_picture"></span><span class="mw-headline" id="Today's_featured_picture">Today's featured picture</span></h2>
<h2 class="mp-h2" id="mp-other"><span class="mw-headline" id="Other_areas_of_Wikipedia">Other areas

In [14]:
def getMovieDetails(url):
    data = {}
    r = requests.get(url=url)
    # Create a BeautifulSoup object
    soup = BeautifulSoup(r.text, 'html.parser')

    #page title
    title = soup.find('title')
    data["title"] = title.string

    # rating
    ratingValue = soup.find("span", {"itemprop" : "ratingValue"})
    data["ratingValue"] = ratingValue.string

    # no of rating given
    ratingCount = soup.find("span", {"itemprop" : "ratingCount"})
    data["ratingCount"] = ratingCount.string

    # name
    titleName = soup.find("div",{'class':'titleBar'}).find("h1")
    data["name"] = titleName.contents[0].replace(u'\xa0', u'')

    # additional details
    subtext = soup.find("div",{'class':'subtext'})
    data["subtext"] = ""
    for i in subtext.contents:
        data["subtext"] += i.string.strip()

    # summary
    summary_text = soup.find("div",{'class':'summary_text'})
    data["summary_text"] = summary_text.string.strip()

    credit_summary_item = soup.find_all("div",{'class':'credit_summary_item'})
    data["credits"] = {}
    for i in credit_summary_item:
        item = i.find("h4")
        names = i.find_all("a")
        data["credits"][item.string] = []
        for i in names:
            data["credits"][item.string].append({
                "link": i["href"],
                "name": i.string
            })
    return data

In [23]:
from bs4 import BeautifulSoup
import requests
import re

# Download IMDB's Top 250 data
url = 'http://www.imdb.com/chart/top'
response = requests.get(url)
soup = BeautifulSoup(response.text, 'lxml')

movies = soup.select('td.titleColumn')
links = [a.attrs.get('href') for a in soup.select('td.titleColumn a')]
crew = [a.attrs.get('title') for a in soup.select('td.titleColumn a')]
ratings = [b.attrs.get('data-value') for b in soup.select('td.posterColumn span[name=ir]')]
votes = [b.attrs.get('data-value') for b in soup.select('td.ratingColumn strong')]

imdb = []
for index in range(0, len(movies)):
    # Seperate movie into: 'place', 'title', 'year'
    movie_string = movies[index].get_text()
    movie = (' '.join(movie_string.split()).replace('.', ''))
    movie_title = movie[len(str(index))+1:-7]
    year = re.search('\((.*?)\)', movie_string).group(1)
    place = movie[:len(str(index))-(len(movie))]
    data = {"movie_title": movie_title,
            "year": year,
            "place": place,
            "star_cast": crew[index],
            "rating": ratings[index],
            "vote": votes[index],
            "link": links[index]}
    imdb.append(data)
    for item in imdb:
        print(item['place'], '-', item['movie_title'], '('+item['year']+') -', 'Starring:', item['star_cast'])


1 - The Shawshank Redemption (1994) - Starring: Frank Darabont (dir.), Tim Robbins, Morgan Freeman
1 - The Shawshank Redemption (1994) - Starring: Frank Darabont (dir.), Tim Robbins, Morgan Freeman
2 - The Godfather (1972) - Starring: Francis Ford Coppola (dir.), Marlon Brando, Al Pacino
1 - The Shawshank Redemption (1994) - Starring: Frank Darabont (dir.), Tim Robbins, Morgan Freeman
2 - The Godfather (1972) - Starring: Francis Ford Coppola (dir.), Marlon Brando, Al Pacino
3 - The Dark Knight (2008) - Starring: Christopher Nolan (dir.), Christian Bale, Heath Ledger
1 - The Shawshank Redemption (1994) - Starring: Frank Darabont (dir.), Tim Robbins, Morgan Freeman
2 - The Godfather (1972) - Starring: Francis Ford Coppola (dir.), Marlon Brando, Al Pacino
3 - The Dark Knight (2008) - Starring: Christopher Nolan (dir.), Christian Bale, Heath Ledger
4 - The Godfather Part II (1974) - Starring: Francis Ford Coppola (dir.), Al Pacino, Robert De Niro
1 - The Shawshank Redemption (1994) - Starr

In [24]:
from bs4 import BeautifulSoup
import requests
import re

# Download IMDB's Top 250 data
url = 'https://www.imdb.com/india/top-rated-indian-movies/'
response = requests.get(url)
soup = BeautifulSoup(response.text, 'lxml')

movies = soup.select('td.titleColumn')
links = [a.attrs.get('href') for a in soup.select('td.titleColumn a')]
crew = [a.attrs.get('title') for a in soup.select('td.titleColumn a')]
ratings = [b.attrs.get('data-value') for b in soup.select('td.posterColumn span[name=ir]')]
votes = [b.attrs.get('data-value') for b in soup.select('td.ratingColumn strong')]

imdb = []
for index in range(0, len(movies)):
    # Seperate movie into: 'place', 'title', 'year'
    movie_string = movies[index].get_text()
    movie = (' '.join(movie_string.split()).replace('.', ''))
    movie_title = movie[len(str(index))+1:-7]
    year = re.search('\((.*?)\)', movie_string).group(1)
    place = movie[:len(str(index))-(len(movie))]
    data = {"movie_title": movie_title,
            "year": year,
            "place": place,
            "star_cast": crew[index],
            "rating": ratings[index],
            "vote": votes[index],
            "link": links[index]}
    imdb.append(data)
    for item in imdb:
        print(item['place'], '-', item['movie_title'], '('+item['year']+') -', 'Starring:', item['star_cast'])


1 - Jai Bhim (2021) - Starring: T.J. Gnanavel (dir.), Suriya, Lijo Mol Jose
1 - Jai Bhim (2021) - Starring: T.J. Gnanavel (dir.), Suriya, Lijo Mol Jose
2 - Anbe Sivam (2003) - Starring: Sundar C. (dir.), Kamal Haasan, Madhavan
1 - Jai Bhim (2021) - Starring: T.J. Gnanavel (dir.), Suriya, Lijo Mol Jose
2 - Anbe Sivam (2003) - Starring: Sundar C. (dir.), Kamal Haasan, Madhavan
3 - Golmaal (1979) - Starring: Hrishikesh Mukherjee (dir.), Amol Palekar, Bindiya Goswami
1 - Jai Bhim (2021) - Starring: T.J. Gnanavel (dir.), Suriya, Lijo Mol Jose
2 - Anbe Sivam (2003) - Starring: Sundar C. (dir.), Kamal Haasan, Madhavan
3 - Golmaal (1979) - Starring: Hrishikesh Mukherjee (dir.), Amol Palekar, Bindiya Goswami
4 - Nayakan (1987) - Starring: Mani Ratnam (dir.), Kamal Haasan, Saranya Ponvannan
1 - Jai Bhim (2021) - Starring: T.J. Gnanavel (dir.), Suriya, Lijo Mol Jose
2 - Anbe Sivam (2003) - Starring: Sundar C. (dir.), Kamal Haasan, Madhavan
3 - Golmaal (1979) - Starring: Hrishikesh Mukherjee (dir.

In [29]:
from bs4 import BeautifulSoup
import requests
url = requests.get('https://presidentofindia.nic.in/former-presidents.htm')
page

<Response [200]>

In [30]:
soup=BeautifulSoup(page.content)
soup

<!DOCTYPE html>
<html class="no-js" lang="en">
<head>
<meta charset="utf-8"/>
<title>Wikipedia</title>
<meta content="Wikipedia is a free online encyclopedia, created and edited by volunteers around the world and hosted by the Wikimedia Foundation." name="description"/>
<script>
document.documentElement.className = document.documentElement.className.replace( /(^|\s)no-js(\s|$)/, "$1js-enabled$2" );
</script>
<meta content="initial-scale=1,user-scalable=yes" name="viewport"/>
<link href="/static/apple-touch/wikipedia.png" rel="apple-touch-icon"/>
<link href="/static/favicon/wikipedia.ico" rel="shortcut icon"/>
<link href="//creativecommons.org/licenses/by-sa/3.0/" rel="license"/>
<style>
.sprite{background-image:linear-gradient(transparent,transparent),url(portal/wikipedia.org/assets/img/sprite-e99844f6.svg);background-repeat:no-repeat;display:inline-block;vertical-align:middle}.svg-Commons-logo_sister{background-position:0 0;width:47px;height:47px}.svg-MediaWiki-logo_sister{background-

In [43]:
from bs4 import BeautifulSoup
import requests



def Menu():
	print('\n1. Men \n2. Women\n')
	gen=Gender()
	print('\n1. Team Rankings \n2. Player Ranking\n')
	tp=TeamOrPlayer()
	
	mode=''
	val=''
	
	if gen=='mens':
		print('\n1. Test\n2. ODI\n3. T20\n')
		mode=Mode()

	if tp=='player-rankings':
		if mode=='':
			print('\n1. ODI\n2. T20\n')
			mode=Mode2()
		print('\n1. Batting\n2. Bowling\n3. All-Rounder\n')
		val=Value()
	
	return gen,tp,mode,val


def Gender():
	gender=input('Enter your choice:')
	code={'1':'mens','2':'womens'}

	if gender in code:
		return code[gender]
	
	else:
		print('\nInvalid Input\nTry Again\n')
		return Gender();


def TeamOrPlayer():
	choice=input('Enter your choice:')
	tp={'1':'team-rankings','2':'player-rankings'}
	
	if choice in tp:
		return tp[choice]
	
	else:
		print('\nInvalid Input\nTry Again\n')
		return TeamOrPlayer();

	
def Mode():
	choice=input('Enter your choice:')
	word={'1':'/test','2':'/odi','3':'/t20i'}
	
	if choice in word:
		return word[choice]
	
	else:
		print('\nInvalid Input\nTry Again\n')
		return Choice();


def Mode2():
	choice=input('Enter your choice:')
	word={'1':'/odi','2':'/t20i'}
	
	if choice in word:
		return word[choice]
	
	else:
		print('\nInvalid Input\nTry Again\n')
		return Choice();


def Value():
	choice=input('Enter your choice:')
	val={'1':'batting','2':'bowling','3':'all-rounder'}
	
	if choice in val:
		return val[choice]
	
	else:
		print('\nInvalid Input\nTry Again\n')
		return Value()


def URL():
	gen,tp,mode,val=Menu()
	url='https://www.icc-cricket.com/rankings/'+gen+'/'+tp+mode+'/'+val
	header=gen.upper() +' ' +mode[1:].upper() + ' ' + val.upper()
	print('\n{:<15}  {:<30}\n{:<15}  {:<30}'.format('',tp.upper(),'',header))
	return url,tp


def SOUP(url,tp):
	try:
		res=requests.get(url)
		soup=BeautifulSoup(res.text,'lxml')
		a= soup.find_all('tr',{'class':'table-body'})
		data={}
			
		for i in a :
			team=[]
			name=''
			rating=''

			try:
				rank=int(i.contents[1].text)
			except:
				pass
			
			try:	
				name=i.contents[3].text.replace('\n','')
				name=" ".join(name.split())
				if rank==1 and tp=='player-rankings':
					name=name[0:-3]
			except:
				pass

			try:
				rating=i.contents[9].text
			except:
				if rank==1 :
					rating=i.contents[5].text
				else:
					rating=i.contents[7].text
			
			team.extend([name,rating])
			data[rank]=team
		
		return data

	except:
		return SOUP(url,tp)


def Print(data):
	print('\nRANKING \t TEAM\t\t\t\tRATING')
	for i in sorted(data):
		print('{:<10}       '.format(i),end='')
		for j in range(len(data[i])):
			print('{:<26}'.format(data[i][j]),end='     ')
		print()


def main():
	
	url,tp=URL()
	data=SOUP(url,tp)
	Print(data)	


if __name__=='__main__':
	main()




1. Men 
2. Women

Enter your choice:2

1. Team Rankings 
2. Player Ranking

Enter your choice:1

                 TEAM-RANKINGS                 
                 WOMENS                        

RANKING 	 TEAM				RATING
2                South AfricaSA                 123                            
3                EnglandENG                     118                            
4                IndiaIND                       100                            
5                New ZealandNZ                  97                             
6                West IndiesWI                  92                             
7                BangladeshBAN                  78                             
8                PakistanPAK                    65                             
9                Sri LankaSL                    48                             
10               IrelandIRE                     44                             
11               ZimbabweZIM                    0           

In [49]:
!pip install bs4
!pip install requests

In [50]:
from bs4 import BeautifulSoup
import requests